In [1]:
import numpy as np
import xarray as xr
import pandas as pd 
import sys 
from EchoPro import EchoPro
epro_2019 = EchoPro(init_file_path='./config_files/initialization_config.yml',
                    survey_year_file_path='./config_files/survey_year_2019_config.yml',
                    source=3,
                    bio_data_type=1,
                    age_data_status=1, 
                    exclude_age1=True)

A check of the initialization file needs to be done!
A check of the survey year file needs to be done!
Loading biological data ...


/Users/brandonreyes/UW_work/EchoPro_work/EchoPro/EchoPro/echo_pro.py:273: UserWarning: We are currently using wgt_total from Matlab for CV, change this!
  warnings.warn("We are currently using wgt_total from Matlab for CV, change this!")


In [2]:
krig_mesh = epro_2019.get_kriging_mesh()
fmap = krig_mesh.get_folium_map()

In [3]:
# Plot transect points 
import geopandas
df = epro_2019.final_biomass_table
gdf = geopandas.GeoDataFrame(df, 
                             geometry=geopandas.points_from_xy(df.Longitude, df.Latitude))
gdf = gdf.reset_index()
fmap = krig_mesh.plot_points(fmap, gdf, cmap_column='Transect', color='hex')

# Plot full mesh points 
# fmap = krig_mesh.plot_points(fmap, krig_mesh.mesh_gdf, color='red')

# Plot EchoPro Matlab no extrapolation points 
# import scipy.io
# mat = scipy.io.loadmat('../2019_consolidated_files/no_extrapolated_mesh_2019.mat')
# no_extra_mesh = pd.DataFrame(columns=['Latitude', 'Longitude'])
# no_extra_mesh['Latitude'] = mat['no_extra_mesh'][:, 0]
# no_extra_mesh['Longitude'] = mat['no_extra_mesh'][:, 1]

# geo_no_extra_mesh = geopandas.GeoDataFrame(no_extra_mesh, 
#                                   geometry=geopandas.points_from_xy(
#                                       no_extra_mesh['Longitude'], 
#                                       no_extra_mesh['Latitude']))
# fmap = krig_mesh.plot_points(fmap, geo_no_extra_mesh, color='red')

# Plot smoothed contour points 
fmap = krig_mesh.plot_points(fmap, krig_mesh.smoothed_contour_gdf, color='blue')

In [4]:
# Plot polygon of transects 
import folium
df_tran_mean = df[["Latitude", "Longitude"]].groupby(level=0).mean()

gdf_tran_mean = geopandas.GeoDataFrame(df_tran_mean, 
                                       geometry=geopandas.points_from_xy(df_tran_mean.Longitude, df_tran_mean.Latitude))


gdf = gdf.set_index('Transect')
transect_polygon = krig_mesh.get_polygon_of_transects(gdf, gdf_tran_mean, n_close=4, nm_to_buffer=1.25)


In [6]:
# fmap 
fmap.add_child(folium.GeoJson(transect_polygon))

In [3]:
# lat_INPFC = [np.NINF, 36, 40.5, 43.000, 45.7667, 48.5, 55.0000]  # INPFC
# cva = epro_2019.run_cv_analysis(lat_INPFC, kriged_data=False)
# 0.13282819671923227